In [37]:
import os
import os.path
import sys
import pandas as pd
import numpy as np

In [2]:
LOCAL_PATH = 'data/'
RAW_TRACE = 'CAP_NIC1_00931_20130727230801.dms'
CONV_FILE = 'conv.txt'

In [3]:
if not os.path.exists(LOCAL_PATH + RAW_TRACE):
    if not os.path.exists(LOCAL_PATH):
        os.mkdir(LOCAL_PATH)
    
    import boto3
    import botocore

    BUCKET_NAME = 'edu.nyu.hsn.ddos-data' # replace with your bucket name
    KEY = 'CAP_NIC1_00931_20130727230801.dms' # replace with your object key

    s3 = boto3.resource('s3')

    try:
        s3.Bucket(BUCKET_NAME).download_file(KEY, LOCAL_PATH + RAW_TRACE)
    except botocore.exceptions.ClientError as e:
        if e.response['Error']['Code'] == "404":
            print("The object does not exist.")
        else:
            raise

In [5]:
import subprocess
if not os.path.exists(LOCAL_PATH + CONV_FILE):
    tshark_command = subprocess.Popen('tshark -r {} -q -z conv,tcp > {}'.format(LOCAL_PATH + RAW_TRACE, LOCAL_PATH + CONV_FILE), shell=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    out_data, err_data = tshark_command.communicate()
    out_data, err_data = out_data.decode('utf-8'), err_data.decode('utf-8')
    
    print('output:' + out_data)
    print('error:' + err_data)

output:
error:
** (process:20307): WARNING **: Dissector bug, protocol TDS, in packet 14442: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:20307): WARNING **: Dissector bug, protocol TDS, in packet 28323: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:20307): WARNING **: Dissector bug, protocol TDS, in packet 37894: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:20307): WARNING **: Dissector bug, protocol SMPP, in packet 85588: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:20307): WARNING **: Dissector bug, protocol DCER

In [4]:
with open(LOCAL_PATH + CONV_FILE, 'r') as f:
    tcp_flow_dict = {\
        'src':[],\
        'dst':[],\
        'back_pkt':[],\
        'back_byte':[],\
        'forw_pkt':[],\
        'forw_byte':[],\
        'tot_pkt':[],\
        'tot_byte':[],\
        'rel_start':[],\
        'duration':[]\
    }
    for line in f.readlines()[5:-1]:
        fields = line.split()
        tcp_flow_dict['src'].append(fields[0])
        tcp_flow_dict['dst'].append(fields[2])
        tcp_flow_dict['back_pkt'].append(fields[3])
        tcp_flow_dict['back_byte'].append(fields[4])
        tcp_flow_dict['forw_pkt'].append(fields[5])
        tcp_flow_dict['forw_byte'].append(fields[6])
        tcp_flow_dict['tot_pkt'].append(fields[7])
        tcp_flow_dict['tot_byte'].append(fields[8])
        tcp_flow_dict['rel_start'].append(fields[9])
        tcp_flow_dict['duration'].append(fields[10])

In [6]:
tcp_flow_df = pd.DataFrame(tcp_flow_dict)

In [7]:
tcp_flow_df.shape

(17984, 10)

In [8]:
tcp_flow_df.columns

Index(['back_byte', 'back_pkt', 'dst', 'duration', 'forw_byte', 'forw_pkt',
       'rel_start', 'src', 'tot_byte', 'tot_pkt'],
      dtype='object')

In [36]:
tcp_flow_df.describe()

back_byte back_pkt                dst duration forw_byte forw_pkt  \
count      17984    17984              17984    17984     17984    17984   
unique      2997      334               3775     6262      3398      345   
top            0        0  10.2.15.129:59532   0.0000         0        0   
freq        3818     3818                553      775      3638     3638   

          rel_start               src tot_byte tot_pkt  
count         17984             17984    17984   17984  
unique        17659             15103     4919     482  
top     7.625783000  10.2.4.171:64461     2120       6  
freq              3               178      387    1640

In [33]:
for sampling_percentage in range(100,10,-20):
    tcp_flow_df.sample(frac=sampling_percentage/100.0).reset_index(drop=True).to_csv('{}flow_{}%.csv'.format(LOCAL_PATH,sampling_percentage), index=False)

In [1]:
!tshark -r data/CAP_NIC1_00931_20130727230801.dms -Y "frame.number & 0x1" -w data/simple_packet-based-50%.pcap -F pcap


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 14442: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 28323: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 37894: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol SMPP, in packet 85588: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in packet 11547


** (process:1872): WARNING **: Dissector bug, protocol TNS, in packet 380417: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in packet 425368: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol SMPP, in packet 488369: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 493059: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 4


** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in packet 670257: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol SMPP, in packet 703040: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 776122: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 795482: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 7


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 997749: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 997756: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 997815: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1056510: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1058


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1138122: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1138126: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1138128: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1138130: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 1

...


** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in packet 2908545: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 2912430: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 2925100: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 2925588: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packe


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3040765: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3040830: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3040837: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3040847: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3193499: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3193545: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3193561: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3193586: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in packe


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3316382: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3316409: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3316418: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3316425: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3


** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3356173: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3356202: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol TDS, in packet 3356217: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in packet 3372142: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1872): WARNING **: Dissector bug, protocol DCERPC, in pa

In [2]:
!ls -la data/

total 2060880
drwxr-xr-x  13 shuojiang  staff        416 Feb 12 22:45 .
drwxr-xr-x  13 shuojiang  staff        416 Feb 12 22:49 ..
-rw-r--r--   1 shuojiang  staff  552075264 Feb  2 21:43 CAP_NIC1_00931_20130727230801.dms
-rw-r--r--   1 shuojiang  staff    2572206 Feb  3 00:36 conv.txt
-rw-r--r--   1 shuojiang  staff    1309302 Feb  3 14:19 flow_100%.csv
-rw-r--r--   1 shuojiang  staff     262259 Feb  3 14:19 flow_20%.csv
-rw-r--r--   1 shuojiang  staff     523605 Feb  3 14:19 flow_40%.csv
-rw-r--r--   1 shuojiang  staff     785848 Feb  3 14:19 flow_60%.csv
-rw-r--r--   1 shuojiang  staff    1047068 Feb  3 14:19 flow_80%.csv
-rw-r--r--   1 shuojiang  staff      15226 Feb  4 15:00 protocol_hier.txt
-rw-r--r--   1 shuojiang  staff  246054336 Feb 12 22:47 simple_packet-based-50%.pcap
-rw-r--r--   1 shuojiang  staff  223312798 Feb  2 22:21 trace.csv
-rw-r--r--   1 shuojiang  staff    2572206 Feb  2 23:13 tshark_conversation.txt


In [6]:
!tshark -r data/simple_packet-based-50%.pcap -T fields -e frame.number | wc -l


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 14162: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 82108: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 82119: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol DCERPC, in packet 93788: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 94341:


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 412153: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 412209: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol SMPP, in packet 417068: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 418891: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 4238


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569072: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569075: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569089: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569109: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 56911


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569660: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569675: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569680: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 569687: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 56968


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 570330: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 570360: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 570362: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 570363: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 57036

...


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1092973: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TNS, in packet 1123443: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol DCERPC, in packet 1129007: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1198023: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packe


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1402013: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1402054: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1407883: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1408029: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1514841: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1514849: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1516170: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1516187: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1636714: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1638804: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1638808: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1646871: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1


** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1691586: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1694214: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1696341: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1696375: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:1956): WARNING **: Dissector bug, protocol TDS, in packet 1

In [7]:
!tshark -r data/CAP_NIC1_00931_20130727230801.dms -T fields -e frame.number | wc -l


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 14442: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 28323: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 37894: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol SMPP, in packet 85588: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol DCERPC, in packet 11547


** (process:2005): WARNING **: Dissector bug, protocol TNS, in packet 380417: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol DCERPC, in packet 425368: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol SMPP, in packet 488369: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 493059: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 4


** (process:2005): WARNING **: Dissector bug, protocol DCERPC, in packet 670257: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol SMPP, in packet 703040: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 776122: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 795482: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 7


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 997749: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 997756: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 997815: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1056510: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1058


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1138122: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1138126: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1138128: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1138130: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 1

...


** (process:2005): WARNING **: Dissector bug, protocol DCERPC, in packet 2879521: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol DCERPC, in packet 2890701: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 2900532: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 2901068: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in pa


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3008128: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3029594: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3029672: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3029681: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3109154: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3109214: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3116997: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3117009: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3301009: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3301142: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3304043: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3304090: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3


** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3350287: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3350309: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3353810: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3353861: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2005): WARNING **: Dissector bug, protocol TDS, in packet 3

In [8]:
!tshark -r data/simple_packet-based-50%.pcap -q -z conv,tcp > packet_sampled_conv.txt


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 14162: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 82108: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 82119: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol DCERPC, in packet 93788: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 94341:


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 412153: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 412209: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol SMPP, in packet 417068: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 418891: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 4238


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 570166: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 570168: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 570169: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 570178: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 57018


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 576723: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 576725: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 576727: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 576730: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 57673


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 586560: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 586563: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 586564: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 586565: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 58656

...


** (process:2052): WARNING **: Dissector bug, protocol TNS, in packet 1059411: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1080835: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1080877: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1092973: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TNS, in packet 1


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1399993: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1400135: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1402013: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1402054: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1503629: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1503667: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1503669: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1514841: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1


** (process:2052): WARNING **: Dissector bug, protocol DCERPC, in packet 1635884: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1636714: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1638804: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1638808: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packe


** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1689346: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1691586: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1694214: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1696341: /Users/buildslave/Documents/wireshark-2.4/osx106x64/build/epan/dissectors/packet-tcp.c:3415: failed assertion "proto_desegment && pinfo->can_desegment"

** (process:2052): WARNING **: Dissector bug, protocol TDS, in packet 1

In [9]:
with open('data/' + 'packet_sampled_conv.txt', 'r') as f:
    tcp_flow_dict = {\
        'src':[],\
        'dst':[],\
        'back_pkt':[],\
        'back_byte':[],\
        'forw_pkt':[],\
        'forw_byte':[],\
        'tot_pkt':[],\
        'tot_byte':[],\
        'rel_start':[],\
        'duration':[]\
    }
    for line in f.readlines()[5:-1]:
        fields = line.split()
        tcp_flow_dict['src'].append(fields[0])
        tcp_flow_dict['dst'].append(fields[2])
        tcp_flow_dict['back_pkt'].append(fields[3])
        tcp_flow_dict['back_byte'].append(fields[4])
        tcp_flow_dict['forw_pkt'].append(fields[5])
        tcp_flow_dict['forw_byte'].append(fields[6])
        tcp_flow_dict['tot_pkt'].append(fields[7])
        tcp_flow_dict['tot_byte'].append(fields[8])
        tcp_flow_dict['rel_start'].append(fields[9])
        tcp_flow_dict['duration'].append(fields[10])

In [11]:
import pandas as pd
tcp_flow_df = pd.DataFrame(tcp_flow_dict)
tcp_flow_df.reset_index(drop=True).to_csv('data/packet_50%.csv', index=False)

In [13]:
pd.read_csv('data/packet_50%.csv').shape

(17246, 10)